# Yelp Restaurants

**[Work in progress]**

This notebook creates a .csv file with yelp information for ingestion into the Knowledge Graph.

In [5]:
import os
import json
import pandas as pd

from pathlib import Path
from yelpapi import YelpAPI
from pprint import pprint

In [6]:
# read yelp api key
with open('key.data', 'r') as key:
    api_key = key.read()

yelp_api = YelpAPI(api_key)

In [7]:
def float_range(start, stop, step):
    while round(start, 6) < stop:
        yield float(round(start, 6))
        start += step

In [8]:
term = 'restaurant'

# 1 degree: approximately 111 km
# using step size of 0.009 degree
start_latitude = 32.550 # 32.670 # 32.710
stop_latitude = 33.100 # 32.770 # 32.750
step_latitude = 0.018

# 1 degree: approximaely 93 km
# using step size of 0.010 degree
start_longitude = -117.260 # -117.260 # -117.175
stop_longitude = -116.900 # -117.100 # -117.140
step_longitude = 0.020

# radius of search 500m
radius = 1000

# yelp api offset and limit
offset = 0
limit = 50

In [9]:
zone = list()
for lat in float_range(start_latitude, stop_latitude, step_latitude * 1.3):
    for long in float_range(start_longitude, stop_longitude, step_longitude):
        zone.append((lat, long))
        
for lat in float_range(start_latitude + step_latitude/1.45, stop_latitude, step_latitude * 1.3):
    for long in float_range(start_longitude + step_longitude/2, stop_longitude, step_longitude):
        zone.append((lat, long))
        
print('Number of coordinates: {}'.format(len(zone)))

Number of coordinates: 846


In [10]:
import folium
import random as rnd

zone_center = [
    round((start_latitude + stop_latitude - step_latitude) / 2, 3), 
    round((start_longitude + stop_longitude - step_longitude) / 2, 3)
]
print(zone_center)

# Build map 
map_zone = folium.Map(location=zone_center, zoom_start=10, tiles='cartodbpositron', width=800, height=600)

# folium.CircleMarker(zone_center, radius=1, color='#00FF00', fill_color='#0080bb').add_to(map_zone)
folium.Rectangle(zone, color='#0080bb', fill_color='#0080bb').add_to(map_zone)

for i in range(len(zone)):
    folium.CircleMarker(zone[i], radius=1, color='#FF0000', fill_color='#0080bb').add_to(map_zone)
    folium.Circle(zone[i], radius=radius, color='#FF0000', fill_color='#0080bb').add_to(map_zone)

map_zone

[32.816, -117.09]


In [110]:
def scrap_yelp(df_combined, latitude, longitude, radius):
    # Maximum 1000 businesses can be pulled
    scrapped = 0
    for i in range(20):
        print('\tScrapping offset: {}'.format(50 * i))
        response = yelp_api.search_query(term=term, latitude=latitude, longitude=longitude, 
                                         limit=limit, radius=radius, offset=scrapped)
        scrapped += len(response['businesses'])
        df = pd.json_normalize(response['businesses'])    

        if df_combined is not None:
            df_combined = pd.concat([df_combined, df], sort=False, ignore_index=True)
        else:       
            df_combined = df.copy()

        # More to scrapped from this location
        if response['total'] <= scrapped:
            print('Completed scrapping. Total: {}'.format(response['total']))
            break
    return df_combined.copy()

In [111]:
df_business = None 
for latitude, longitude in zone:
    print('Scrapping coordinate: ({}, {}). Radius: {}'.format(latitude, longitude, radius))
    df_business = scrap_yelp(df_business, latitude, longitude, radius)

Scrapping coordinate: (32.55, -117.26). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.24). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.22). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.2). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.18). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.16). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.14). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.12). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.1). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.55, -117.08). Radius: 1000
	Scrapping of

Completed scrapping. Total: 0
Scrapping coordinate: (32.6436, -117.14). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.6436, -117.12). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.6436, -117.1). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 35
Scrapping coordinate: (32.6436, -117.08). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 27
Scrapping coordinate: (32.6436, -117.06). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 16
Scrapping coordinate: (32.6436, -117.04). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 9
Scrapping coordinate: (32.6436, -117.02). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 8
Scrapping coordinate: (32.6436, -117.0). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 26
Scrapping coordinate: (32.6436, -116.98). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coor

Completed scrapping. Total: 11
Scrapping coordinate: (32.7372, -117.08). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 3
Scrapping coordinate: (32.7372, -117.06). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 10
Scrapping coordinate: (32.7372, -117.04). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 40
Scrapping coordinate: (32.7372, -117.02). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 20
Scrapping coordinate: (32.7372, -117.0). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 4
Scrapping coordinate: (32.7372, -116.98). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 5
Scrapping coordinate: (32.7372, -116.96). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 5
Scrapping coordinate: (32.7372, -116.94). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 29
Scrapping coordinate: (32.7372, -116.92). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 9
Scrapping co

Completed scrapping. Total: 0
Scrapping coordinate: (32.8308, -117.02). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 5
Scrapping coordinate: (32.8308, -117.0). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 17
Scrapping coordinate: (32.8308, -116.98). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 38
Scrapping coordinate: (32.8308, -116.96). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 9
Scrapping coordinate: (32.8308, -116.94). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 3
Scrapping coordinate: (32.8308, -116.92). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.8542, -117.26). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 20
Scrapping coordinate: (32.8542, -117.24). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (32.8542, -117.22). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 10
Scrapping coo

Completed scrapping. Total: 0
Scrapping coordinate: (32.9244, -116.92). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.9478, -117.26). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 9
Scrapping coordinate: (32.9478, -117.24). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 49
Scrapping coordinate: (32.9478, -117.22). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 8
Scrapping coordinate: (32.9478, -117.2). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 5
Scrapping coordinate: (32.9478, -117.18). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.9478, -117.16). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.9478, -117.14). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.9478, -117.12). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 2
Scrapping coordi

...

Completed scrapping. Total: 3
Scrapping coordinate: (32.679414, -116.99). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.679414, -116.97). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.679414, -116.95). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 2
Scrapping coordinate: (32.679414, -116.93). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.679414, -116.91). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.702814, -117.25). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (32.702814, -117.23). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 2
Scrapping coordinate: (32.702814, -117.21). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 4
Scrapping coordinate: (32.702814, -117.19). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 

Completed scrapping. Total: 48
Scrapping coordinate: (32.773014, -117.01). Radius: 1000
	Scrapping offset: 0
	Scrapping offset: 50
Completed scrapping. Total: 65
Scrapping coordinate: (32.773014, -116.99). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 5
Scrapping coordinate: (32.773014, -116.97). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (32.773014, -116.95). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 6
Scrapping coordinate: (32.773014, -116.93). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 5
Scrapping coordinate: (32.773014, -116.91). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.796414, -117.25). Radius: 1000
	Scrapping offset: 0
	Scrapping offset: 50
	Scrapping offset: 100
Completed scrapping. Total: 128
Scrapping coordinate: (32.796414, -117.23). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 46
Scrapping coordinate: (32.796414, 

Completed scrapping. Total: 0
Scrapping coordinate: (32.866614, -116.95). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.866614, -116.93). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 11
Scrapping coordinate: (32.866614, -116.91). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 2
Scrapping coordinate: (32.890014, -117.25). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 10
Scrapping coordinate: (32.890014, -117.23). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 14
Scrapping coordinate: (32.890014, -117.21). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 31
Scrapping coordinate: (32.890014, -117.19). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 7
Scrapping coordinate: (32.890014, -117.17). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 6
Scrapping coordinate: (32.890014, -117.15). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Tot

Completed scrapping. Total: 25
Scrapping coordinate: (32.983614, -117.23). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (32.983614, -117.21). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (32.983614, -117.19). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 6
Scrapping coordinate: (32.983614, -117.17). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (32.983614, -117.15). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (32.983614, -117.13). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.983614, -117.11). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (32.983614, -117.09). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 18
Scrapping coordinate: (32.983614, -117.07). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total

Completed scrapping. Total: 0
Scrapping coordinate: (33.077214, -117.15). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (33.077214, -117.13). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (33.077214, -117.11). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (33.077214, -117.09). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (33.077214, -117.07). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 26
Scrapping coordinate: (33.077214, -117.05). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (33.077214, -117.03). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 1
Scrapping coordinate: (33.077214, -117.01). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total: 0
Scrapping coordinate: (33.077214, -116.99). Radius: 1000
	Scrapping offset: 0
Completed scrapping. Total:

In [177]:
len(df_business)

9755

In [180]:
df_business = df_business.drop_duplicates(subset=['id'])

In [181]:
len(df_business)

6065

In [182]:
columns={
    'coordinates.latitude':'coordinates_latitude',
    'coordinates.longitude':'coordinates_longitude',    
    'location.address1':'location_address1',
    'location.address2':'location_address2',
    'location.address3':'location_address3',
    'location.city':'location_city',
    'location.zip_code':'location_zip_code',
    'location.country':'location_country',
    'location.state':'location_state',
    'location.display_address':'location_display_address',
}
df_business_final = df_business.rename(columns=columns)

In [183]:
df_business_final.head()

id                               alias  \
0  AJ1SJkAVv1H6lA4pDnZ0dQ       ying-li-restaurant-san-ysidro   
1  uGt9jvS6tcPpYhJa1kDl1w     la-cachonda-cenaduria-san-diego   
2  9BeEPZ4p0iEHYyKLYBLRBw               zappy-pizza-san-diego   
3  Ws4nOG8u2uSTUqEA28a30Q              tropifrutas-san-ysidro   
4  bN2HUTEFnzSKVJI4dxvkhQ  robertacos-mexican-food-san-ysidro   

                      name                                          image_url  \
0       Ying Li Restaurant  https://s3-media2.fl.yelpcdn.com/bphoto/YJPpJz...   
1    La Cachonda Cenaduria  https://s3-media2.fl.yelpcdn.com/bphoto/orODHq...   
2              Zappy Pizza  https://s3-media2.fl.yelpcdn.com/bphoto/FTn7AB...   
3              Tropifrutas  https://s3-media1.fl.yelpcdn.com/bphoto/SA-nYT...   
4  Robertacos Mexican Food  https://s3-media3.fl.yelpcdn.com/bphoto/saJgJY...   

   is_closed                                                url  review_count  \
0      False  https://www.yelp.com/biz/ying-li-restaurant-sa...           163   
1      False  https://www.yelp.com/biz/la-cachonda-cenaduria...             3   
2      False  https://www.yelp.com/biz/zappy-pizza-san-diego...            32   
3      False  https://www.yelp.com/biz/tropifrutas-san-ysidr...           132   
4      False  https://www.yelp.com/biz/robertacos-mexican-fo...            99   

                                          categories  rating  \
0         [{'alias': 'chinese', 'title': 'Chinese'}]     4.0   
1         [{'alias': 'mexican', 'title': 'Mexican'}]     4.0   
2             [{'alias': 'pizza', 'title': 'Pizza'}]     4.0   
3  [{'alias': 'sandwiches', 'title': 'Sandwiches'...     2.5   
4         [{'alias': 'mexican', 'title': 'Mexican'}]     2.0   

         transactions  ... coordinates_latitude coordinates_longitude  \
0  [pickup, delivery]  ...            32.554284           -117.050823   
1          [delivery]  ...            32.555684           -117.051453   
2  [pickup, delivery]  ...            32.554764           -117.052038   
3  [pickup, delivery]  ...            32.554350           -117.050650   
4          [delivery]  ...            32.555960           -117.054950   

       location_address1  location_address2  location_address3  location_city  \
0  342 W San Ysidro Blvd                                           San Ysidro   
1  347 W San Ysidro Blvd               None                         San Diego   
2  416 W San Ysidro Blvd                                            San Diego   
3  342 W San Ysidro Blvd                                           San Ysidro   
4  492 W San Ysidro Blvd                                           San Ysidro   

  location_zip_code location_country location_state  \
0             92173               US             CA   
1             92173               US             CA   
2             92173               US             CA   
3             92173               US             CA   
4             92173               US             CA   

                        location_display_address  
0  [342 W San Ysidro Blvd, San Ysidro, CA 92173]  
1   [347 W San Ysidro Blvd, San Diego, CA 92173]  
2   [416 W San Ysidro Blvd, San Diego, CA 92173]  
3  [342 W San Ysidro Blvd, San Ysidro, CA 92173]  
4  [492 W San Ysidro Blvd, San Ysidro, CA 92173]  

[5 rows x 24 columns]

In [185]:
with open('./../../data/yelp_restaurant.csv', 'w') as f:
    df_business_final.to_csv(f, index=False)

In [197]:
df_csv = pd.read_csv('./../../data/yelp_restaurant.csv')

In [198]:
df_coordinates = df_csv[['coordinates_latitude', 'coordinates_longitude']].dropna()

In [199]:
# Build map 
map_zone = folium.Map(location=zone_center, zoom_start=10, tiles='cartodbpositron', width=800, height=600)
for i in range(len(df_coordinates)):
    folium.CircleMarker((df_coordinates.iloc[i][0], df_coordinates.iloc[i][1]), 
                        radius=1, color='#FF0000', fill_color='#0080bb').add_to(map_zone)
map_zone

In [257]:
len(df_csv)

6065

In [258]:
# df_review = None
start_again = False
for i, business_id in enumerate(df_csv['id']):
    if not start_again:
        if business_id == 'ah0g8YxYJRlNtCv29LWyMQ': #'4mRXrCvYv0ynViY5TiGBkQ':
            start_again = True
    else:
        response = yelp_api.reviews_query(id=business_id)
        df = pd.json_normalize(response['reviews'])
        df.insert(0, 'business_id', business_id) 

        if df_review is not None:
            df_review = pd.concat([df_review, df], sort=False, ignore_index=True)
        else:       
            df_review = df.copy()
    
    if i % 100 == 0:
        print('Processing business #{}'.format(i + 1))

Processing business #1
Processing business #101
Processing business #201
Processing business #301
Processing business #401
Processing business #501
Processing business #601
Processing business #701
Processing business #801
Processing business #901
Processing business #1001
Processing business #1101
Processing business #1201
Processing business #1301
Processing business #1401
Processing business #1501
Processing business #1601
Processing business #1701
Processing business #1801
Processing business #1901
Processing business #2001
Processing business #2101
Processing business #2201
Processing business #2301
Processing business #2401
Processing business #2501
Processing business #2601
Processing business #2701
Processing business #2801
Processing business #2901
Processing business #3001
Processing business #3101
Processing business #3201
Processing business #3301
Processing business #3401
Processing business #3501
Processing business #3601
Processing business #3701
Processing business #380

In [259]:
len(df_review)

17428

In [262]:
df_review.tail(5)

business_id                      id  \
17423  caquwLQ2wuApa618uL3YQg  zfFRjCc9RrGwJP3eNNQ0fQ   
17424  caquwLQ2wuApa618uL3YQg  wAoJ0GG7L9t-3MXbKiYQOQ   
17425  EIC1EkoJMxc3U3LgQY4P7w  MXzM_HCloGVDJ69MTToStQ   
17426  EIC1EkoJMxc3U3LgQY4P7w  X5oKAiqRpkbWs09aYxmacw   
17427  EIC1EkoJMxc3U3LgQY4P7w  0aK67erS6-zNJatphHf_Fw   

                                                     url  \
17423  https://www.yelp.com/biz/cotijas-taco-shop-car...   
17424  https://www.yelp.com/biz/cotijas-taco-shop-car...   
17425  https://www.yelp.com/biz/tacos-chato-carlsbad?...   
17426  https://www.yelp.com/biz/tacos-chato-carlsbad?...   
17427  https://www.yelp.com/biz/tacos-chato-carlsbad?...   

                                                    text  rating  \
17423  Empty - 5:30 on a Thursday....doors open, no o...     1.0   
17424  Man this place got me mad ! I bought some taco...     2.0   
17425  Where do I start? Maybe with the service: the ...     5.0   
17426  Great food, super friendly service. Got lots o...     5.0   
17427  The lady behind the counter is extremely STING...     1.0   

              time_created                 user.id  \
17423  2020-10-08 17:41:34  uD2TVhKdiR56HruXNWxccQ   
17424  2020-07-31 14:20:32  GyBU-ld7Q10j0zXjiDOKuA   
17425  2020-10-27 16:37:16  ZnVBsHRrfxaiUhD719I9Cg   
17426  2020-10-31 15:51:07  n2VgomhnRvHUlrlebYUe0w   
17427  2020-10-12 17:08:07  UMrFBwopp-7u-WTzgrVRlA   

                                        user.profile_url  \
17423  https://www.yelp.com/user_details?userid=uD2TV...   
17424  https://www.yelp.com/user_details?userid=GyBU-...   
17425  https://www.yelp.com/user_details?userid=ZnVBs...   
17426  https://www.yelp.com/user_details?userid=n2Vgo...   
17427  https://www.yelp.com/user_details?userid=UMrFB...   

                                          user.image_url   user.name  
17423  https://s3-media4.fl.yelpcdn.com/photo/Av5iJct...        H S.  
17424  https://s3-media4.fl.yelpcdn.com/photo/5VeyUmX...  Eleazar E.  
17425  https://s3-media2.fl.yelpcdn.com/photo/bxSQ6lM...   DonMia F.  
17426                                               None        M P.  
17427                                               None     Erik I.

In [ ]:
df_review = df_review.drop_duplicates(subset=['id'])

In [263]:
columns={
    'user.id':'user_id',
    'user.profile_url':'user_profile_url',    
    'user.image_url':'user_image_url',
    'user.name':'user_name',
}
df_review_final = df_review.rename(columns=columns)

In [265]:
with open('./../../data/yelp_restaurant_review.csv', 'w') as f:
    df_review_final.to_csv(f, index=False)